<a href="https://colab.research.google.com/github/BrianKEverett/County-Line/blob/main/Final_Everett.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1123]:
!pip install ydata-profiling
from ydata_profiling import ProfileReport

In [1124]:
import time, os, sys, re #basics
import zipfile, json, datetime, string   #string for annotating points in scatter
import numpy as np #basic math
from statistics import * #stats

import matplotlib.pyplot as plt #import pylab as plt #apparently discouraged now:
 #https://stackoverflow.com/questions/11469336/what-is-the-difference-between-pylab-and-pyplot
 #https://www.tutorialspoint.com/matplotlib/matplotlib_pylab_module.htm

import pandas as pd
import pandas_datareader as pdr
from pandas_datareader import wb
from pandas.io.formats.style import Styler
#s4 = Styler(df4, uuid_len=0, cell_ids=False)

import missingno as msno

from google.colab import files

#import webbrowser

import seaborn as sns

from google.colab import data_table
data_table.enable_dataframe_formatter() #this enables spreadsheet view upon calling dataframe (without() )
data_table.max_columns = 50
#!and may have to click at top right spreadsheet icon

#many tricks how to extend notebook functionality
#https://coderzcolumn.com/tutorials/python/list-of-useful-magic-commands-in-jupyter-notebook-lab
#will display all output not just last command
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

#MAGICS and THEMES/STYLES: important! does affect not just shading/colors, but also fonts, spacing, etc
#(even if you only select default (v not selecting anything) [but does seem to work better if you do make explicit sleections])

###magics: https://ipython.readthedocs.io/en/stable/interactive/magics.html
#most essential setup for vis: it does affect vis! careful!! stick with inline, maybe notebook; others mostly for non-notebook, eg spyder environ
#https://jakevdp.github.io/PythonDataScienceHandbook/04.00-introduction-to-matplotlib.html recomends *inline*!
#show current one:
#%matplotlib
#%matplotlib --list
#interactive plots:
#%matplotlib notebook
#static images of your plot:
%matplotlib inline
#may play with this one and other magics (btw default is probably agg)
#%matplotlib nbagg
##https://www.marktechpost.com/2023/10/20/6-magic-commands-for-jupyter-notebooks-in-python-data-science/
#%%latex
#%ai
#%run
#%writefile
#%history -n

###themes/styles: https://matplotlib.org/stable/gallery/style_sheets/style_sheets_reference.html
#https://jakevdp.github.io/PythonDataScienceHandbook/04.11-settings-and-stylesheets.html
#https://matplotlib.org/stable/tutorials/introductory/customizing.html
#here more about art and style than under the hood functionality as with magics, explore and experiment
#many may find 'default' or seaborn ones more pleasing; my fav 'classic' is back from 90s ;)
#plt.style.available #list available styles :) may install more
#plt.style.use('default') # more delicate subtle than classic
plt.style.use('classic')  #  'seaborn-whitegrid' 'seaborn-white' 'seaborn-poster'
# btw: magics v theme/style sequence matters, eg if i specify classic style before inline magic, i wouldnt get grey bounding box im getting

In [1125]:
permits=pd.read_csv("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/Permits.csv")
# dataset can be found here: https://njdca.maps.arcgis.com/home/item.html?id=c754e8f800424bcbb6ad4e6e85b9f736 from NJ Dept of Community Affairs Website.
#this dataset was chosen mostly to assist with my dissertation proposal - I am seeking to explore the behaviors of planning boards in New Jersey, and one hypothesis I have is that planning board decisions are influenced by the effects of the County Line Balloting system, which is unique to 19 out of 21 counties in New Jersey. No other state in the US runs primary elections in this way.
#More on the County Line can be found here by Julia Sass Rubin: https://www.njpp.org/wp-content/uploads/2021/01/NJPP-Report-Does-the-County-Line-Matter-Update-wiht-Final-Vote-Counts.pdf

taxes=pd.read_csv ("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/mediantax.csv")
# dataset can be retireved via: https://njdca.maps.arcgis.com/apps/webappviewer/index.html?id=96ec274c50a34890b23263f101e4ad9b from NJ Department of Community Affairs
# Another hypothesis I have is that the public narrative put forth by planning board members when approving controversial permits, "this will increase rateables for the township, lowering your taxes", does not actually come to fruition
#This data set is helpful for exploring that narrative, and seeing if the opposite is occurring, i.e. more development actually yields higher property taxes

#health=pd.read_csv ("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/countyhealth.csv")
#dataset can be found here: https://www.countyhealthrankings.org/explore-health-rankings/rankings-data-documentation from County Health Rankings and Roadmaps, for 2022 to match same year of data for permits dataset
#With County Health Data, we can infer hypotheses about rates of development and the effect on well-being, liveability.

#Problem with health data set == only 22 observations for New Jersey, not a good sample.

municodes=pd.read_csv ("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/Municodes.csv")
#Data file of all NJ municiaplities, and counties, with the corresponding municipalitiy DCA code. This data file will be most helpful for matching and merging.

#crime=pd.read_csv ("https://raw.githubusercontent.com/BrianKEverett/County-Line/main/CamdenCrime.csv") #not a good format for reading data!
#Dataset can be retireved here: https://www.nj.gov/njsp/ucr/uniform-crime-reports.shtml on the NJ Office of the Attorney General's website
#This crime data is important to consider when analyzing planning and zoning. Does any specific type of development correlate with increased crime? Can liveability theory be worked in here for whether or not communities have what they need to prevent crime?

jobs=pd.read_csv('https://raw.githubusercontent.com/BrianKEverett/County-Line/main/jobsdensity.csv')
#dataset can be built via the table selections on the NJ Community Affairs website - https://njdca.maps.arcgis.com/apps/webappviewer/index.html?id=96ec274c50a34890b23263f101e4ad9b
#Job density is a good variable to consider regarding new large dollar permits. Are some places growing more than others? Can this be attribute to the phenomenon of the County Line?

In [1126]:
permits = permits.rename(columns={'DCA MUNI CODE': 'DCA'})
permits = permits.rename(columns={'MUNICIPALITY': 'Municipality'})
permits["Municipality"]= permits["Municipality"].str.title()
del permits['ID']
del permits['BLOCK NUMBER']
del permits['PAMS PIN']
del permits['USE GROUP']
del permits['YCOORD']
del permits['XCOORD']
del permits['MATCH TYPE']
del permits['LOT NUMBER']
del permits['DATE ISSUED'] #play around with this one to see if it helps to make graphs
del permits['TAX CODE']

permits = permits.rename(columns={'DCA MUNI CODE': 'DCA'})
permits = permits.rename(columns={'MUNICIPALITY': 'Municipality'})
permits = permits.rename(columns={'WORK VALUE': 'value'})
permits = permits.set_index('Municipality')

del municodes['MUNICIPALITY_NAME_NJ-1040']
del municodes['MUNICIPALITY_CODE_DCA']
del municodes['MUNICIPALITY_NAME_DCA']
del municodes['MUNICIPALITY_CODE_GNIS']
del municodes['MUNICIPALITY_NAME_GNIS']
del municodes['MUNICIPALITY_CODE_FIPS']
municodes = municodes.rename(columns={'MUNICIPALITY_NAME_COMMON': 'Municipality'})
municodes = municodes.rename(columns={'MUNICIPALITY_CODE_NJ-1040': 'DCA'})
municodes = municodes.rename(columns={'COUNTY_NAME_COMMON': 'County'})
municodes['County'] = municodes['County'].str.replace(' County', '')
municodes = municodes.set_index('Municipality')

del jobs['Blk_Grp_Name']
del jobs['JobsVintage']
#del jobs['Jobs']
jobs = jobs.set_index('Municipality')

del taxes['Data_Vintage']
del taxes['Tract_Name']
taxes = taxes.rename(columns={'Median_RE_Taxes': 'MedianTax'})
taxes = taxes[['County', 'Municipality', 'MedianTax']]
taxes = taxes.set_index('Municipality')


In [1127]:
permits["value"] = permits["value"].str.replace(",","").astype(float)

In [1128]:
permits["value"].astype(np.int64)

Municipality
Absecon City        695000
Absecon City       4000000
Atlantic City      2100000
Atlantic City      2100000
Atlantic City       337400
                    ...   
Washington Boro    1000000
Washington Twp      426124
Washington Twp      742000
Washington Twp      276000
Washington Twp      515000
Name: value, Length: 9783, dtype: int64

In [1129]:
permits
permits.drop_duplicates()

DCA                                    Use Group Label TYPE  \
Municipality                                                                    
Absecon City      101                                         Mercantile  NEW   
Absecon City      101                                        Educational  ALT   
Atlantic City     102  Clubs, Dance Halls, Casinos, Restaurants, Tave...  ALT   
Atlantic City     102                   Residential (1 & 2 Family Homes)  ALT   
Atlantic City     102    Churches, Libraries, Arcades, Comm. Halls, Gyms  ALT   
...               ...                                                ...  ...   
Washington Boro  2121                   Residential (1 & 2 Family Homes)  ALT   
Washington Twp   2122                   Residential (1 & 2 Family Homes)  ALT   
Washington Twp   2122                                        Educational  ALT   
Washington Twp   2122                                           Business  ALT   
Washington Twp   2122                                           Business  ALT   

                     value  
Municipality                
Absecon City      695000.0  
Absecon City     4000000.0  
Atlantic City    2100000.0  
Atlantic City    2100000.0  
Atlantic City     337400.0  
...                    ...  
Washington Boro  1000000.0  
Washington Twp    426124.0  
Washington Twp    742000.0  
Washington Twp    276000.0  
Washington Twp    515000.0  

[9783 rows x 4 columns]

DCA                                    Use Group Label TYPE  \
Municipality                                                                    
Absecon City      101                                         Mercantile  NEW   
Absecon City      101                                        Educational  ALT   
Atlantic City     102  Clubs, Dance Halls, Casinos, Restaurants, Tave...  ALT   
Atlantic City     102                   Residential (1 & 2 Family Homes)  ALT   
Atlantic City     102    Churches, Libraries, Arcades, Comm. Halls, Gyms  ALT   
...               ...                                                ...  ...   
Washington Boro  2121                   Residential (1 & 2 Family Homes)  ALT   
Washington Twp   2122                   Residential (1 & 2 Family Homes)  ALT   
Washington Twp   2122                                        Educational  ALT   
Washington Twp   2122                                           Business  ALT   
Washington Twp   2122                                           Business  ALT   

                     value  
Municipality                
Absecon City      695000.0  
Absecon City     4000000.0  
Atlantic City    2100000.0  
Atlantic City    2100000.0  
Atlantic City     337400.0  
...                    ...  
Washington Boro  1000000.0  
Washington Twp    426124.0  
Washington Twp    742000.0  
Washington Twp    276000.0  
Washington Twp    515000.0  

[9089 rows x 4 columns]

In [1130]:
slim = permits[['DCA', 'value']]
slim

DCA      value
Municipality                    
Absecon City      101   695000.0
Absecon City      101  4000000.0
Atlantic City     102  2100000.0
Atlantic City     102  2100000.0
Atlantic City     102   337400.0
...               ...        ...
Washington Boro  2121  1000000.0
Washington Twp   2122   426124.0
Washington Twp   2122   742000.0
Washington Twp   2122   276000.0
Washington Twp   2122   515000.0

[9783 rows x 2 columns]

In [1131]:
municodes

County   DCA
Municipality                        
Absecon               Atlantic   101
Atlantic City         Atlantic   102
Brigantine            Atlantic   103
Buena Borough         Atlantic   104
Buena Vista Township  Atlantic   105
...                        ...   ...
Phillipsburg            Warren  2119
Pohatcong Township      Warren  2120
Washington Borough      Warren  2121
Washington Township     Warren  2122
White Township          Warren  2123

[564 rows x 2 columns]

In [1132]:
codespermits = pd.merge(municodes, slim, left_on=["Municipality", "DCA" ], right_on=["Municipality", "DCA"])
print(codespermits)
#codespermits = pd.merge(municodes, slim, how='inner', on=['DCA', 'Municipality'],indicator=True)

                 County  DCA      value
Municipality                           
Atlantic City  Atlantic  102  2100000.0
Atlantic City  Atlantic  102  2100000.0
Atlantic City  Atlantic  102   337400.0
Atlantic City  Atlantic  102  2217000.0
Atlantic City  Atlantic  102   555200.0
...                 ...  ...        ...
Union City       Hudson  910   258345.0
Union City       Hudson  910   360950.0
Union City       Hudson  910  8331000.0
Union City       Hudson  910   403500.0
Union City       Hudson  910   546300.0

[846 rows x 3 columns]


In [1133]:
codespermits.drop_duplicates()

County  DCA      value
Municipality                           
Atlantic City  Atlantic  102  2100000.0
Atlantic City  Atlantic  102   337400.0
Atlantic City  Atlantic  102  2217000.0
Atlantic City  Atlantic  102   555200.0
Atlantic City  Atlantic  102  2076500.0
...                 ...  ...        ...
Union City       Hudson  910   258345.0
Union City       Hudson  910   360950.0
Union City       Hudson  910  8331000.0
Union City       Hudson  910   403500.0
Union City       Hudson  910   546300.0

[718 rows x 3 columns]

In [1134]:
codespermits.value_counts()

County    DCA  value    
Cape May  509  252650.0     11
Hudson    906  300000.0      7
Cape May  509  252500.0      7
Hudson    906  250000.0      6
               400000.0      5
                            ..
Cape May  508  258250.0      1
               261000.0      1
               273000.0      1
               275000.0      1
Hudson    910  8331000.0     1
Length: 718, dtype: int64

In [1135]:
codespermits

County  DCA      value
Municipality                           
Atlantic City  Atlantic  102  2100000.0
Atlantic City  Atlantic  102  2100000.0
Atlantic City  Atlantic  102   337400.0
Atlantic City  Atlantic  102  2217000.0
Atlantic City  Atlantic  102   555200.0
...                 ...  ...        ...
Union City       Hudson  910   258345.0
Union City       Hudson  910   360950.0
Union City       Hudson  910  8331000.0
Union City       Hudson  910   403500.0
Union City       Hudson  910   546300.0

[846 rows x 3 columns]

In [1136]:
jobs

County  Jobs  JobsDensity
Municipality                                         
West Caldwell Township       Essex  4376  4219.922635
West Caldwell Township       Essex    28    85.385941
West Caldwell Township       Essex  1939  1640.631286
Monroe Township         Gloucester   226   589.619454
West Deptford Township  Gloucester   156   258.364616
...                            ...   ...          ...
Marlboro Township         Monmouth    90   107.930966
Marlboro Township         Monmouth   243   233.244240
Marlboro Township         Monmouth  2738   745.848682
Dumont Borough              Bergen    10    80.075270
Dumont Borough              Bergen   592  6652.557850

[2000 rows x 3 columns]

In [1137]:
jobspermits = pd.merge(codespermits, jobs, left_on=["Municipality", "County" ], right_on=["Municipality", "County"], indicator=True)
#jobspermits = pd.merge(codespermits, jobs, how='inner', on=['County'],indicator=True)

In [1138]:
jobspermits

County  DCA     value  Jobs   JobsDensity _merge
Municipality                                                     
Gloucester City  Camden  414  600000.0   234   2828.199868   both
Gloucester City  Camden  414  600000.0   587   3052.966496   both
Gloucester City  Camden  414  600000.0   533   6103.257410   both
Gloucester City  Camden  414  600000.0   974   2379.170020   both
Gloucester City  Camden  414  600000.0   441   1353.714438   both
...                 ...  ...       ...   ...           ...    ...
Union City       Hudson  910  403500.0    76   2829.627348   both
Union City       Hudson  910  546300.0    67   3114.045285   both
Union City       Hudson  910  546300.0   539  17694.996971   both
Union City       Hudson  910  546300.0    24    833.635917   both
Union City       Hudson  910  546300.0    76   2829.627348   both

[38001 rows x 6 columns]

In [1139]:
jobspermits.value_counts()

County  DCA  value      Jobs  JobsDensity   _merge
Hudson  906  300000.0   120   1561.787063   both      7
                        232   7372.315820   both      7
                        41    1231.275291   both      7
                        42    1151.148807   both      7
                              4766.040518   both      7
                                                     ..
             444880.0   80    1587.838390   both      1
                        72    2807.421813   both      1
                        71    6525.093460   both      1
                        70    1612.259396   both      1
        910  8331000.0  539   17694.996971  both      1
Length: 30576, dtype: int64

In [1140]:
jobspermits.drop_duplicates()

County  DCA     value  Jobs   JobsDensity _merge
Municipality                                                     
Gloucester City  Camden  414  600000.0   234   2828.199868   both
Gloucester City  Camden  414  600000.0   587   3052.966496   both
Gloucester City  Camden  414  600000.0   533   6103.257410   both
Gloucester City  Camden  414  600000.0   974   2379.170020   both
Gloucester City  Camden  414  600000.0   441   1353.714438   both
...                 ...  ...       ...   ...           ...    ...
Union City       Hudson  910  403500.0    76   2829.627348   both
Union City       Hudson  910  546300.0    67   3114.045285   both
Union City       Hudson  910  546300.0   539  17694.996971   both
Union City       Hudson  910  546300.0    24    833.635917   both
Union City       Hudson  910  546300.0    76   2829.627348   both

[30576 rows x 6 columns]

In [1141]:
del jobspermits ['_merge']
jobspermits

County  DCA     value  Jobs   JobsDensity
Municipality                                              
Gloucester City  Camden  414  600000.0   234   2828.199868
Gloucester City  Camden  414  600000.0   587   3052.966496
Gloucester City  Camden  414  600000.0   533   6103.257410
Gloucester City  Camden  414  600000.0   974   2379.170020
Gloucester City  Camden  414  600000.0   441   1353.714438
...                 ...  ...       ...   ...           ...
Union City       Hudson  910  403500.0    76   2829.627348
Union City       Hudson  910  546300.0    67   3114.045285
Union City       Hudson  910  546300.0   539  17694.996971
Union City       Hudson  910  546300.0    24    833.635917
Union City       Hudson  910  546300.0    76   2829.627348

[38001 rows x 5 columns]

In [1142]:
taxes

County  MedianTax
Municipality                              
Bridgewater Township   Somerset    10000.0
Bernards Township      Somerset    10000.0
Franklin Township      Somerset     9604.0
Woodbridge Township   Middlesex     9041.0
Woodbridge Township   Middlesex     7496.0
...                         ...        ...
Franklin Township      Somerset    10000.0
Franklin Township      Somerset     6600.0
Franklin Township      Somerset    10000.0
Bernards Township      Somerset    10000.0
Bernards Township      Somerset    10000.0

[1646 rows x 2 columns]

In [1143]:
final = pd.merge(jobspermits, taxes, on=['Municipality', 'County'],indicator=False)
#final = pd.merge(jobspermits, taxes, left_on=["Municipality", "County" ], right_on=["Municipality", "County"])
#final.drop_duplicates()

In [1144]:
final

County  DCA      value  Jobs  JobsDensity  MedianTax
Municipality                                                      
Jersey City   Hudson  906  1095360.0    41   638.945018     8423.0
Jersey City   Hudson  906  1095360.0    41   638.945018     6872.0
Jersey City   Hudson  906  1095360.0    41   638.945018    10000.0
Jersey City   Hudson  906  1095360.0    41   638.945018    10000.0
Jersey City   Hudson  906  1095360.0    41   638.945018     4214.0
...              ...  ...        ...   ...          ...        ...
Union City    Hudson  910   546300.0    76  2829.627348     9977.0
Union City    Hudson  910   546300.0    76  2829.627348    10000.0
Union City    Hudson  910   546300.0    76  2829.627348     8478.0
Union City    Hudson  910   546300.0    76  2829.627348    10000.0
Union City    Hudson  910   546300.0    76  2829.627348    10000.0

[2920761 rows x 6 columns]

##go back and delete the Jobs column, retry merge on left or right to reduce number of total rows / duplicate rows&columns. That might be the trick!